# 使用说明：
    1.需要修改chdir到当前目录
    2.需要修改最后输出的文件名称
    3.依据情况需要修改保留的列数
    4.不同品种的交易时间不一样，要修改删除

In [ ]:
import pandas as pd
import numpy as np
import os
import datetime as datetime

In [ ]:
os.chdir('E:/data/ru')
all_csv_files = [file for file in os.listdir('.') if file.endswith('.csv')]
all_csv_files = sorted(all_csv_files)
print("文件中所有CSV文件:",all_csv_files)

sp_old_chars = ['_2019','_2020','_2021']
sp_old_chars = sorted(sp_old_chars)
print("旧格式文件名关键字:",sp_old_chars)
sp_new_chars = ['_2022','_2023']
sp_new_chars = sorted(sp_new_chars)
print("新格式文件名关键字:",sp_new_chars)

# # 设置后面数据的采集对于的行数# 用 "old_type" 或者 "new_type" 区分
# if all(char in ['_2019','_2020','_2021'] for char in sp_old_chars):
#     year_type = 'old_type'
#     print("使用旧年份格式采集!!!")
# elif all(char in ['_2022','_2023'] for char in sp_chars):
#     year_type = 'new_type' 
#     print("使用新年份格式采集!!!")
# else:
#     print("文件夹中CSV没有相关年份的数据或者新旧年份混用!!!")

csv_old_files = [file for file in all_csv_files if any(sp_char in file for sp_char in sp_old_chars)]
print("筛选结果后的CSV文件:",csv_old_files)
csv_new_files = [file for file in all_csv_files if any(sp_char in file for sp_char in sp_new_chars)]
print("筛选结果后的CSV文件:",csv_new_files)

In [ ]:
df_old = pd.DataFrame()
for f in csv_old_files:
    df_old_temp = pd.read_csv(
        f,
        usecols=[1, 2, 3, 4, 8, 13, 14, 15, 16],
        names=[
            "统一代码",
            "合约代码",
            "时间",
            "最新",
            "成交量",
            "买一价",
            "卖一价",
            "买一量",
            "卖一量",
        ],
        skiprows=1,
        encoding="utf-8",
        parse_dates=['时间']#注意此处增加的排序，为了后面按时间排序
    )
    # df_temp = pd.read_csv(f, usecols=[0,5], names=[
    #                  'datetime',  'volume'])
    df_old = pd.concat([df_old, df_old_temp])
del df_old_temp

In [ ]:
df_old =pd.DataFrame({'main_contract':df_old['统一代码'],'symbol':df_old['合约代码'],'datetime':df_old['时间'],'lastprice':df_old['最新'],'volume':df_old['成交量'],
           'bid_p':df_old['买一价'],'ask_p':df_old['卖一价'],'bid_v':df_old['买一量'],'ask_v':df_old['卖一量']})

In [ ]:
df_old['time'] = df_old['datetime'].dt.strftime('%H:%M:%S')

In [ ]:
df_old.info()

In [ ]:
df_old.tail()

In [ ]:
# 不同品种交易时间不一样，需要修改
# 商品期货
drop_index1 = df_old.query('time>"15:00:00" & time<"21:00:00"')["time"].index
# drop_index1 = df_old.query('time>"15:00:00"')["time"].index
# drop_index2 = df_old.query('time>"01:00:00" & time<"09:00:00"')["time"].index
#drop_index2 = df_old.query('time>"02:30:00" & time<"09:00:00"')["time"].index
drop_index2 = df_old.query('time<"09:00:00"')["time"].index
drop_index3 = df_old.query('time>"23:00:00" & time<"23:59:59"')["time"].index
# drop_index3 = df_old.query('time>"11:30:00" & time<"13:30:00"')["time"].index
drop_index4 = df_old.query('time>"10:15:00" & time<"10:30:00"')["time"].index

# 清理不在交易时间段的数据
df_old.drop(labels=drop_index1, axis=0, inplace=True)
df_old.drop(drop_index2, axis=0, inplace=True)
df_old.drop(drop_index3, axis=0, inplace=True)
df_old.drop(drop_index4, axis=0, inplace=True)

df_old.info()

In [ ]:
df_old.tail()

In [ ]:
del df_old['time']

In [ ]:
df_old.tail()

In [ ]:
df_new = pd.DataFrame()
for f in csv_new_files:
    df_new_temp = pd.read_csv(
    f,
    usecols=[0, 1, 2, 5, 12, 21, 22, 23, 24, 25, 26, 44],
    names=[
        "交易日",
        "统一代码",
        "合约代码",
        "最新价",
        "数量",
        "最后修改时间",
        "最后修改毫秒",
        "申买价一",
        "申买量一",
        "申卖价一",
        "申卖量一",
        "业务日期",
    ],
    skiprows=1,
    encoding="utf-8",
    parse_dates=['业务日期','最后修改时间','最后修改毫秒']#注意此处增加的排序，为了后面按时间排序
    )

    # df_temp = pd.read_csv(f, usecols=[0,5], names=[
    #                  'datetime',  'volume'])
    df_new = pd.concat([df_new, df_new_temp])
del df_new_temp

In [ ]:
# 不同品种交易时间不一样，需要修改
# 商品期货
drop_index1 = df_new.query('最后修改时间>"15:00:00" & 最后修改时间<"21:00:00"')["最后修改时间"].index
# drop_index1 = df_new.query('最后修改时间>"15:00:00"')["最后修改时间"].index
# drop_index2 = df_new.query('最后修改时间>"01:00:00" & 最后修改时间<"09:00:00"')["最后修改时间"].index
# drop_index2 = df_new.query('最后修改时间>"02:30:00" & 最后修改时间<"09:00:00"')["最后修改时间"].index
drop_index2 = df_new.query('最后修改时间<"09:00:00"')["最后修改时间"].index
drop_index3 = df_new.query('最后修改时间>"23:00:00" & 最后修改时间<"23:59:59"')["最后修改时间"].index
# drop_index3 = df_new.query('最后修改时间>"11:30:00" & 最后修改时间<"13:30:00"')["最后修改时间"].index
drop_index4 = df_new.query('最后修改时间>"10:15:00" & 最后修改时间<"10:30:00"')["最后修改时间"].index

# 清理不在交易时间段的数据
df_new.drop(labels=drop_index1, axis=0, inplace=True)
df_new.drop(drop_index2, axis=0, inplace=True)
df_new.drop(drop_index3, axis=0, inplace=True)
df_new.drop(drop_index4, axis=0, inplace=True)

df_new.info()

In [ ]:
#日期修正
#df_new['业务日期'] = pd.to_datetime(df_new['业务日期'])
df_new['业务日期'] = df_new['业务日期'].dt.strftime('%Y-%m-%d')
df_new['datetime'] = df_new['业务日期'] + ' '+df_new['最后修改时间'].dt.time.astype(str) + '.' + df_new['最后修改毫秒'].astype(str)
# 将 'datetime' 列的数据类型更改为 datetime 格式，如果数据转换少8个小时，可以用timedelta处理
df_new['datetime'] = pd.to_datetime(df_new['datetime'], errors='coerce', format='%Y-%m-%d %H:%M:%S.%f')
# 如果需要，可以将 datetime 列格式化为字符串
#df_new['formatted_date'] = df_new['datetime'].dt.strftime('%Y-%m-%d %H:%M:%S.%f')
#计算瞬时成交量
df_new['volume'] = df_new['数量'] - df_new['数量'].shift(1)
df_new['volume'] = df_new['volume'].fillna(0)

In [ ]:
df_new =pd.DataFrame({'main_contract':df_new['统一代码'],'symbol':df_new['合约代码'],'datetime':df_new['datetime'],'lastprice':df_new['最新价'],'volume':df_new['volume'],
           'bid_p':df_new['申买价一'],'ask_p':df_new['申卖价一'],'bid_v':df_new['申买量一'],'ask_v':df_new['申卖量一']})

In [ ]:
df_old.head()

In [ ]:
df_old.tail()

In [ ]:
df_new.head()

In [ ]:
df_new.tail()

In [ ]:
df = pd.DataFrame()
df = pd.concat([df_old, df_new],axis=0, ignore_index=True)

In [ ]:
del df_old,df_new

In [ ]:
df['main_contract'] = df['main_contract'].astype(str)
df['symbol'] = df['symbol'].astype(str)
df['datetime'] = pd.to_datetime(df['datetime'], errors='coerce', format='%Y-%m-%d %H:%M:%S.%f')
df['lastprice'] = df['lastprice'].astype(float)
df['volume'] = df['volume'].astype(int)
df['bid_p'] = df['bid_p'].astype(float)
df['ask_p'] = df['ask_p'].astype(float)
df['bid_v'] = df['bid_v'].astype(int)
df['ask_v'] = df['ask_v'].astype(int)
#df = df_old.append(df_new, ignore_index=True)

In [ ]:
df.head()

In [ ]:
df.tail()

In [ ]:
df.info()

In [ ]:
# 删除重复行
df.drop_duplicates(inplace=True)

In [ ]:
# 确保日期列按升序排序
df.sort_values(by='datetime', inplace=True)

# 查看数据的头部和尾部：head()、tail()

In [ ]:
df.reset_index(drop=True, inplace=True)

In [ ]:
# 查看dataframe的基本情况
df.info()

# 等比复权,先不考虑
# df['复权因子'] = df['卖一价'].shift() / df['买一价']
df['复权因子'] = np.where(df['合约代码'] != df['合约代码'].shift(), df['卖一价'].shift() / df['买一价'], 1)
df['复权因子'] = df['复权因子'].fillna(1)
# df['复权因子'].loc[0] = 1
df['买一价_adj'] = df['买一价'] * df['复权因子'].cumprod()
df['卖一价_adj'] = df['卖一价'] * df['复权因子'].cumprod()
df['最新_adj'] = df['最新'] * df['复权因子'].cumprod()
# df['low_adj'] = df['low'] * adjust.cumprod()
# df['high_adj'] = df['high'] * adjust.cumprod()

In [ ]:
# 等差复权
df['复权因子'] = np.where(df['symbol'] != df['symbol'].shift(), df['ask_p'].shift() - df['bid_p'], 0)
df['复权因子'] = df['复权因子'].fillna(0)
# df['复权因子'].loc[0] = 1
df['bid_p_adj'] = df['bid_p'] + df['复权因子'].cumsum()
df['ask_p_adj'] = df['ask_p'] + df['复权因子'].cumsum()
df['lastprice_adj'] = df['lastprice'] + df['复权因子'].cumsum()
# df['low_adj'] = df['low'] + df['复权因子'].cumsum()
# df['high_adj'] = df['high'] + df['复权因子'].cumsum()
# df_new =pd.DataFrame({'main_contract':df_new['统一代码'],'symbol':df_new['合约代码'],'datetime':df_new['datetime'],'lastprice':df_new['最新价'],'volume':df_new['volume'],
#            'bid_p':df_new['申买价一'],'ask_p':df_new['申卖量一'],'bid_v':df_new['申买量一'],'ask_v':df_new['申卖量一']})

In [ ]:
print(df['复权因子'])

In [ ]:
contains_null = df.isnull().values.any()

In [ ]:
print(contains_null)

In [ ]:
# 查找换期需要复权的索引
non_zero_indices = df[df['复权因子'] != 0].index
print(non_zero_indices)

In [ ]:
# 查看未调整买价、卖价和最新价的数据
df.loc[non_zero_indices[0]-5:non_zero_indices[0]+5]

In [ ]:
# 将调整后的数值替换原来的值
df['bid_p'] = df['bid_p_adj']
df['ask_p'] = df['ask_p_adj']
df['lastprice'] = df['lastprice_adj']


In [ ]:
# 查看调整买价、卖价和最新价的数据
df.loc[non_zero_indices[0]-5:non_zero_indices[0]+5]

In [ ]:
# 删除多余的值
del df['复权因子']
del df['bid_p_adj']
del df['ask_p_adj']
del df['lastprice_adj']

In [ ]:
df.head()

In [ ]:
df.tail()

In [ ]:
df.loc[non_zero_indices[0]-5:non_zero_indices[0]+5]

In [ ]:
df.to_csv('./ru888.csv', index=False)

In [ ]:
del df

In [1]:
import pandas as pd
import numpy as np
import os
import datetime as datetime
import pyarrow as pa
import pyarrow.feather as feather

In [3]:
# feature 测试
df = pd.read_csv('E:/data/ru/ru888.csv',encoding='UTF-8',parse_dates=['datetime'])

In [5]:
feather.write_feather(df, 'df_feather.feather')

In [6]:
df = feather.read_feather('df_feather.feather')

In [7]:
df.tail()

main_contract  symbol                datetime  lastprice  volume  \
44287432         ru888  ru2405 2023-12-29 14:59:58.500     6755.0      27   
44287433         ru888  ru2405 2023-12-29 14:59:59.000     6760.0      27   
44287434         ru888  ru2405 2023-12-29 14:59:59.500     6760.0      17   
44287435         ru888  ru2405 2023-12-29 15:00:00.000     6760.0       6   
44287436         ru888  ru2405 2023-12-29 15:00:00.500     6760.0       0   

           bid_p   ask_p  bid_v  ask_v  
44287432  6750.0  6755.0    128     15  
44287433  6755.0  6760.0      2     14  
44287434  6760.0  6765.0     35     33  
44287435  6760.0  6765.0     45     42  
44287436  6760.0  6765.0     45     42